In [1]:
%matplotlib inline
import matplotlib.pyplot as plt
import numpy as np
import os
from scipy.ndimage import imread
from scipy import signal
import librosa as lbr
import IPython.display as ipd
import time
from tensorlayer.layers import *
import tensorlayer as tl
import tensorflow as tf
import argparse
from collections import namedtuple
import pprint
from random import shuffle

/Users/hongbozhu/anaconda3/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


In [2]:
os.chdir("/Users/hongbozhu/Desktop/6104 project/genres/blues")

In [3]:
def read_data(genre_A, genre_B, base_path="/Users/hongbozhu/Desktop/6104 project/genres/"):
    start_time=time.time()
    genre_A_path=base_path+str(genre_A)
    genre_B_path=base_path+str(genre_B)
    genre_A_song_path=os.listdir(genre_A_path)
    genre_A_song_path=[genre_A_path+"/"+i for i in genre_A_song_path]
    genre_B_song_path=os.listdir(genre_B_path)
    genre_B_song_path=[genre_B_path+"/"+i for i in genre_B_song_path]
    
#     def stft_transfer(song_path):
#         song, sr = lbr.load(song_path,sr=None)
#         f,t,song=signal.stft(song,fs=22050,nfft=512,nperseg=512)
#         song=np.log(song)
#         return song
    def matrix_song(song_path):
        song,sr=lbr.load(song_path,sr=None)
        song=np.asarray(song[:-32594])
        return song.reshape([-1,220,220])
    genre_A=list(map(matrix_song,genre_A_song_path[0:2]))
    genre_B=list(map(matrix_song,genre_B_song_path[0:2]))
    print("time spend is: ", time.time()-start_time)
    return genre_A, genre_B

genre_a,genre_b=read_data("blues","classical")


time spend is:  1.4489622116088867


In [4]:
13*220*220

629200

In [5]:


A=[ image for song in genre_a for image in song ]
B=[ image for song in genre_a for image in song ]
train_A= np.asarray(A[0:13]).reshape([13,220,220,1])
test_A=np.asarray(A[13:]).reshape([13,220,220,1])
train_B=np.asarray(B[0:13]).reshape([13,220,220,1])
test_B=np.asarray(B[13:]).reshape([13,220,220,1])

#A=np.asarray(A)
#A=np.concatenate(A[:10],1)
q=train_A.reshape([629200])
# kk=np.exp(gen_B_temp_out.reshape([257,258]))
#b,q=signal.istft(kk, fs=22050,nfft=512,nperseg=512)
ipd.Audio(q,rate=22050)

(220, 220, 1)

In [28]:

def cyclegan_generator_resnet(image, num=9, is_train=True, reuse=False, batch_size=None, name='generator'):
    b_init = tf.constant_initializer(value=0.0)
    w_init = tf.truncated_normal_initializer(stddev=0.02)
    g_init = tf.random_normal_initializer(1., 0.02)
    with tf.variable_scope(name, reuse=reuse):
        tl.layers.set_name_reuse(reuse)
        gf_dim = 10

        net_in = InputLayer(image, name='in')
        # net_pad = PadLayer(net_in, [[0, 0], [3, 3], [3, 3], [0, 0]], "REFLECT", name='inpad')

        net_c1 = Conv2d(net_in, gf_dim, (7, 7), (1, 1), act=None,
                padding='SAME', W_init=w_init, name='c7s1-10')  # c7s1-10   shape:(1,257,258,10)
        net_c1 = InstanceNormLayer(net_c1, act=tf.nn.relu, name='ins1')

        net_c2 = Conv2d(net_c1, gf_dim * 2, (3, 3), (2, 2), act=None,
                padding='SAME', W_init=w_init,name='c20')  # d64   shape:(1,129,129,20)
        net_c2 = InstanceNormLayer(net_c2, act=tf.nn.relu, name='ins2')

        net_c3 = Conv2d(net_c2, gf_dim * 4, (3, 3), (2, 2), act=None,
                padding='SAME', W_init=w_init, name='c40')  # d128   shape(1,65,65,40)
        net_c3 = InstanceNormLayer(net_c3, act=tf.nn.relu, name='ins3')

        n = net_c3
        for i in range(num):
            # n_pad = PadLayer(n, [[0, 0], [1, 1], [1, 1], [0, 0]], "REFLECT", name='pad_%s' % i)
            nn = Conv2d(n, gf_dim * 4, (3, 3), (1, 1), act=None,
                padding='SAME', W_init=w_init, b_init=b_init, name='res/c1/%s' % i)
            nn = InstanceNormLayer(nn, act=tf.nn.relu, name='res/ins/%s' % i)

            # nn = PadLayer(nn, [[0, 0], [1, 1], [1, 1], [0, 0]], "REFLECT", name='pad2_%s' % i)
            nn = Conv2d(nn, gf_dim * 4, (3, 3), (1, 1), act=None,
                padding='SAME', W_init=w_init, b_init=b_init, name='res/c2/%s' % i)
            nn = InstanceNormLayer(nn, name='res/ins2/%s' % i)

            nn = ElementwiseLayer([n, nn], tf.add, name='b_residual_add/%s' % i)
            n = nn

        net_r9 = n
        net_d1 = DeConv2d(net_r9, gf_dim * 2, (3, 3),
            strides=(2, 2), padding='SAME', batch_size=batch_size, act=None, name='u64')  # u64
        net_d1 = InstanceNormLayer(net_d1, act=tf.nn.relu, name='inso1')

        net_d2 = DeConv2d(net_d1, gf_dim, (3, 3),
            strides=(2, 2), padding='SAME',batch_size=batch_size, act=None, name='u32')  # u32
        net_d2 = InstanceNormLayer(net_d2, act=tf.nn.relu, name='inso2')

        # net_d2_pad = PadLayer(net_d2, [[0, 0], [3, 3], [3, 3], [0, 0]], "REFLECT", name='pado')
        net_d3 = Conv2d(net_d2, 1, (7, 7), (1, 1), act=tf.nn.tanh,
            padding='SAME', name='c7s1-3')  # c7s1-3
        out=net_d3.outputs[:,:220,:220,:]
        
    return net_d3, out


def cyclegan_discriminator_patch(inputs,num=4, is_train=True, reuse=False, name='discriminator'):
    df_dim = 10  # Dimension of discrim filters in first conv layer. [32]
    b_init = tf.constant_initializer(value=0.0)
    w_init = tf.random_normal_initializer(stddev=0.02)
    gamma_init = tf.random_normal_initializer(1., 0.02)
    lrelu = lambda x: tl.act.lrelu(x, 0.2)
    with tf.variable_scope(name, reuse=reuse):
        tl.layers.set_name_reuse(reuse)
        net_in = InputLayer(inputs, name='d/in')

        net_c1 = Conv2d(net_in, df_dim, (7, 7), (1, 1), act=None,
                padding='SAME', W_init=w_init, name='c7s1-10')  # c7s1-10   shape:(1,256,256,10)
        net_c1 = InstanceNormLayer(net_c1, act=tf.nn.relu, name='ins1')

        net_c2 = Conv2d(net_c1, df_dim * 2, (3, 3), (2, 2), act=None,
                padding='SAME', W_init=w_init,name='d20')  # d20   shape:(1,128,128,20)
        net_c2 = InstanceNormLayer(net_c2, act=tf.nn.relu, name='ins2')

        net_c3 = Conv2d(net_c2, df_dim * 4, (3, 3), (2, 2), act=None,
                padding='SAME', W_init=w_init, name='d40')  # d40   shape(1,64,64,40)
        net_c3 = InstanceNormLayer(net_c3, act=tf.nn.relu, name='ins3')

        n = net_c3
        for i in range(num):
            # n_pad = PadLayer(n, [[0, 0], [1, 1], [1, 1], [0, 0]], "REFLECT", name='pad_%s' % i)
            
            n = Conv2d(n, df_dim * 4*2**i, (3, 3), (2, 2), act=None, #shape 32->16->8->4
                padding='SAME', W_init=w_init, b_init=b_init, name='res/c1/%s' % i)
            
            n = InstanceNormLayer(n, act=tf.nn.relu, name='res/ins1/%s' % i)


            nn = Conv2d(n, df_dim * 4*2**i, (3, 3), (1, 1), act=None,
                padding='SAME', W_init=w_init, b_init=b_init, name='res/c2/%s' % i)
            nn = InstanceNormLayer(nn, act=tf.nn.relu, name='res/ins2/%s' % i)

            # nn = PadLayer(nn, [[0, 0], [1, 1], [1, 1], [0, 0]], "REFLECT", name='pad2_%s' % i)
            nn = Conv2d(nn, df_dim * 4*2**i, (3, 3), (1, 1), act=None,
                padding='SAME', W_init=w_init, b_init=b_init, name='res/c3/%s' % i)
            nn = InstanceNormLayer(nn, name='res/ins3/%s' % i)

            nn = ElementwiseLayer([n, nn], tf.add, name='b_residual_add/%s' % i)
            n = nn
        # output
        flatten = FlattenLayer(n, name='d/h4/flatten')
        
        final_net = DenseLayer(flatten, n_units=1, act=tf.identity,
                W_init = w_init, name='d/h4/final')
        
        logits = final_net.outputs



    return final_net, logits



In [15]:
tf.reset_default_graph()

In [13]:
# pp = pprint.PrettyPrinter()
# flags = tf.app.flags
# flags.DEFINE_integer("epoch", 10, "Epoch to train [100]")
# flags.DEFINE_float("learning_rate", 0.0002, "Learning rate of for adam [0.0002]")
# flags.DEFINE_float("beta1", 0.5, "Momentum term of adam [0.5]")
# flags.DEFINE_float("weight_decay", 1e-5, "Weight decay for l2 loss")
# flags.DEFINE_float("pool_size", 50, 'size of image buffer that stores previously generated images, default: 50')
# #flags.DEFINE_integer("train_size", np.inf, "The size of train images [np.inf]")
# flags.DEFINE_integer("batch_size", 1, "The number of batch images [1] if we use InstanceNormLayer !")
# flags.DEFINE_string("dataset_dir", "horse2zebra", "The name of dataset [horse2zebra, apple2orange, sunflower2daisy and etc]")
# flags.DEFINE_string("checkpoint_dir", "checkpoint", "Directory name to save the checkpoints [checkpoint]")
# flags.DEFINE_string("sample_dir", "samples", "Directory name to save the image samples [samples]")
# flags.DEFINE_string("direction", "forward", "The direction of generator [forward, backward]")
# flags.DEFINE_string("test_dir", "./test", "The direction of test")
# flags.DEFINE_boolean("is_train", True, "True for training, False for testing [False]")
# flags.DEFINE_boolean("is_crop", False, "True for training, False for testing [False]")
# # flags.DEFINE_boolean("visualize", False, "True for visualizing, False for nothing [False]")
# FLAGS = flags.FLAGS

tf.reset_default_graph()

epoch=5
learning_rate=0.0002
beta1=0.5
weight_decay=1e-5
pool_size=50
batch_size=1
train_size=100

sess = tf.Session()

ni = int(np.sqrt(batch_size))


lamda=1


real_A = tf.placeholder(tf.float32, [1,220,220,1],
                        name='real_A')
real_B = tf.placeholder(tf.float32, [1,220,220,1],
                        name='real_B')
fake_A_pool = tf.placeholder(tf.float32,[1,220,220,1],
                        name='fake_A')
fake_B_pool = tf.placeholder(tf.float32,[1,220,220,1],
                        name='fake_B')

gen_B, gen_B_out = cyclegan_generator_resnet(real_A, 9, is_train=True, reuse=False, name='gen_A2B')
gen_A, gen_A_out = cyclegan_generator_resnet(real_B, 9, is_train=True, reuse=False, name='gen_B2A')
cyc_B, cyc_B_out = cyclegan_generator_resnet(gen_A_out, 9, is_train=True, reuse=True, name='gen_A2B')
cyc_A, cyc_A_out = cyclegan_generator_resnet(gen_B_out, 9, is_train=True, reuse=True, name='gen_B2A')

d_real_A, d_real_A_logits = cyclegan_discriminator_patch(real_A, is_train=True, reuse=False, name='dis_A')  # dx
d_real_B, d_real_B_logits = cyclegan_discriminator_patch(real_B, is_train=True, reuse=False, name='dis_B')  # dy
d_fake_A, d_fake_A_logits = cyclegan_discriminator_patch(gen_A_out, is_train=True, reuse=True, name='dis_A')  # d_fy
d_fake_B, d_fake_B_logits = cyclegan_discriminator_patch(gen_B_out, is_train=True, reuse=True, name='dis_B')  # d_gx

#d_A_pool, d_A_pool_logits = cyclegan_discriminator_patch(fake_A_pool, is_train=True, reuse=True, name='dis_A')  # d_fakex
#d_B_pool, d_B_pool_logits = cyclegan_discriminator_patch(fake_B_pool, is_train=True, reuse=True, name='dis_B')  # d_fakey

    
## calculate cycle loss
cyc_loss = tf.reduce_mean(tf.abs(cyc_A_out - real_A)) + tf.reduce_mean(tf.abs(cyc_B_out - real_B))

## calculate adversial loss
g_loss_A2B = tf.reduce_mean(tl.cost.sigmoid_cross_entropy(d_fake_B_logits, tf.ones_like(d_fake_B_logits)), name='g_loss_b')
    # g_loss_A2B = tf.reduce_mean(tf.reduce_mean(tf.squared_difference(d_fake_B, tf.ones_like(d_fake_B)), [1, 2, 3]), name='g_loss_b')

g_loss_B2A = tf.reduce_mean(tl.cost.sigmoid_cross_entropy(d_fake_A_logits, tf.ones_like(d_fake_A_logits),name='g_loss_a'))
    # g_loss_B2A = tf.reduce_mean(tf.reduce_mean(tf.squared_difference(d_fake_A, tf.ones_like(d_fake_A)), [1, 2, 3]), name='g_loss_a')

## calculate totalloss of generator
g_a2b_loss = lamda * cyc_loss + (1-lamda)* g_loss_A2B  # forward
g_b2a_loss = lamda * cyc_loss +(1-lamda)* g_loss_B2A  # backward


d_a_loss_real = tf.reduce_mean(tl.cost.sigmoid_cross_entropy(d_real_A_logits, tf.ones_like(d_real_A_logits)))
# discriminator: images from generator (fake) are labelled as 0
d_a_loss_fake = tf.reduce_mean(tl.cost.sigmoid_cross_entropy(d_fake_A_logits, tf.zeros_like(d_fake_A_logits)))
d_a_loss = d_a_loss_real + d_a_loss_fake

d_b_loss_real = tf.reduce_mean(tl.cost.sigmoid_cross_entropy(d_real_B_logits, tf.ones_like(d_real_B_logits)))
# discriminator: images from generator (fake) are labelled as 0
d_b_loss_fake = tf.reduce_mean(tl.cost.sigmoid_cross_entropy(d_fake_B_logits, tf.zeros_like(d_fake_B_logits)))
d_b_loss = d_b_loss_real + d_b_loss_fake



g_A2B_vars = tl.layers.get_variables_with_name('gen_A2B', True, True)
g_B2A_vars = tl.layers.get_variables_with_name('gen_B2A', True, True)
d_A_vars = tl.layers.get_variables_with_name('dis_A', True, True)
d_B_vars = tl.layers.get_variables_with_name('dis_B', True, True)

# with tf.device('/gpu:0'):
with tf.variable_scope('learning_rate'):
    lr_v = tf.Variable(learning_rate, trainable=False)
# g_a2b_optim = tf.train.AdamOptimizer(lr_v, beta1=beta1).minimize(g_a2b_loss, var_list=g_A2B_vars)
# g_b2a_optim = tf.train.AdamOptimizer(lr_v, beta1=beta1).minimize(g_b2a_loss, var_list=g_B2A_vars)
# d_a_optim = tf.train.AdamOptimizer(lr_v, beta1=beta1).minimize(d_a_loss, var_list=d_A_vars)
# d_b_optim = tf.train.AdamOptimizer(lr_v, beta1=beta1).minimize(d_b_loss, var_list=d_B_vars)
cyc_loss_optim=tf.train.AdamOptimizer(lr_v, beta1=beta1).minimize(cyc_loss)

## init params
tl.layers.initialize_global_variables(sess)

# net_g_A2B_name = os.path.join(FLAGS.checkpoint_dir, '{}_net_g_A2B.npz'.format(FLAGS.dataset_dir))
# net_g_B2A_name = os.path.join(FLAGS.checkpoint_dir, '{}_net_g_B2A.npz'.format(FLAGS.dataset_dir))
# net_d_A_name = os.path.join(FLAGS.checkpoint_dir, '{}_net_d_A.npz'.format(FLAGS.dataset_dir))
# net_d_B_name = os.path.join(FLAGS.checkpoint_dir, '{}_net_d_B.npz'.format(FLAGS.dataset_dir))

# tl.files.load_and_assign_npz(sess=sess, name=net_g_A2B_name, network=gen_B)
# tl.files.load_and_assign_npz(sess=sess, name=net_g_B2A_name, network=gen_A)
# tl.files.load_and_assign_npz(sess=sess, name=net_d_A_name, network=d_fake_A)
# tl.files.load_and_assign_npz(sess=sess, name=net_d_B_name, network=d_fake_B)

##========================= TRAIN MODELS ================================##
iter_counter = 1
start_time = time.time()

dataA,dataB,im_test_A,im_test_b=train_A, train_B, test_A, test_B
# dataA, dataB im_test_A, im_test_B = tl.files.load_cyclegan_dataset(filename=FLAGS.dataset_dir, path='datasets')

# sample_A = np.asarray(dataA[0: 16])
# sample_B = np.asarray(dataB[0: 16])
# sample_A = tl.prepro.threading_data(sample_A, fn=rescale)
# sample_B = tl.prepro.threading_data(sample_B, fn=rescale)

# tl.vis.save_images(sample_A, [4, 4], './{}/sample_A.jpg'.format(FLAGS.sample_dir))
# tl.vis.save_images(sample_B, [4, 4], './{}/sample_B.jpg'.format(FLAGS.sample_dir))

# shuffle(dataA)
# shuffle(dataB)

for epoch in range(epoch):
    ## change learning rate
    if epoch >= 100:
        new_lr = learning_rate - learning_rate * (epoch - 100) / 100
        sess.run(tf.assign(lr_v, new_lr))
        print("New learning rate %f" % new_lr)

    batch_idxs = min(min(len(dataA), len(dataB)), train_size) // batch_size
    for idx in range(0, batch_idxs):
        batch_imgA = dataA[idx * batch_size:(idx + 1) * batch_size] 
        batch_imgB = dataB[idx * batch_size:(idx + 1) * batch_size]

        gen_A_temp_out, gen_B_temp_out = sess.run([gen_A_out, gen_B_out],
                            feed_dict={real_A: batch_imgA, real_B: batch_imgB})

        ## update forward network
        #_, errGA2B = sess.run([g_a2b_optim, g_a2b_loss],
                            #feed_dict={real_A: batch_imgA, real_B: batch_imgB})
        ## update DB network
        #_, errDB = sess.run([d_b_optim, d_b_loss],
                            #feed_dict={real_A: batch_imgA, real_B: batch_imgB, fake_B_pool: gen_B_temp_out})
        ## update (backword) network
        #_, errGB2A = sess.run([g_b2a_optim, g_b2a_loss],
                            #feed_dict={real_A: batch_imgA, real_B: batch_imgB})
        ## update DA network
        #_, errDA = sess.run([d_a_optim, d_a_loss],
                            #feed_dict={real_A: batch_imgA, real_B: batch_imgB, fake_A_pool: gen_A_temp_out})
        _,cycle_loss_temperal=sess.run([cyc_loss_optim, cyc_loss],
                            feed_dict={real_A: batch_imgA, real_B: batch_imgB, fake_A_pool: gen_A_temp_out})

        #print("Epoch: [%2d/%2d] [%4d/%4d] time: %4.4fs, d_a_loss: %.8f, d_b_loss: %.8f, g_a2b_loss: %.8f, g_b2a_loss: %.8f, cycle_loss: %a" \
            #% (epoch, epoch, idx, batch_idxs, time.time() - start_time, errDA, errDB, errGA2B, errGB2A,cycle_loss_temperal))
        print("Epoch: [%2d/%2d] [%4d/%4d] time: %4.4fs, cycle_loss: %a"% (epoch, epoch, idx, batch_idxs, time.time() - start_time, 
                                                                          cycle_loss_temperal)) 
        iter_counter += 1
        # num_fake += 1

#         if np.mod(iter_counter, 500) == 0:
#             oA, oB = sess.run([gen_A_out, gen_B_out],
#                             feed_dict={real_A: sample_A, real_B: sample_B})
#             tl.vis.save_images(oA, [4, 4],
#                                './{}/B2A_{:02d}_{:04d}.jpg'.format(FLAGS.sample_dir, epoch, idx))
#             print("save image gen_A, Epoch: %2d idx:%4d" % (epoch, idx))
#             tl.vis.save_images(oB, [4, 4],
#                                './{}/A2B_{:02d}_{:04d}.jpg'.format(FLAGS.sample_dir, epoch, idx))
#             print("save image gen_B, Epoch: %2d idx:%4d" % (epoch, idx))

#     if (epoch != 0) and (epoch % 10) == 0:
#         tl.files.save_npz(gen_B.all_params, name=net_g_A2B_name, sess=sess)
#         tl.files.save_npz(gen_A.all_params, name=net_g_B2A_name, sess=sess)
#         tl.files.save_npz(d_fake_A.all_params, name=net_d_A_name, sess=sess)
#         tl.files.save_npz(d_fake_B.all_params, name=net_d_B_name, sess=sess)
#         print("[*] Save checkpoints SUCCESS!")




  [TL] InputLayer  gen_A2B/in: (1, 220, 220, 1)
  [TL] Conv2dLayer gen_A2B/c7s1-10: shape:[7, 7, 1, 10] strides:[1, 1, 1, 1] pad:SAME act:identity
  [TL] InstanceNormLayer gen_A2B/ins1: epsilon:0.000010 act:relu
  [TL] Conv2dLayer gen_A2B/c20: shape:[3, 3, 10, 20] strides:[1, 2, 2, 1] pad:SAME act:identity
  [TL] InstanceNormLayer gen_A2B/ins2: epsilon:0.000010 act:relu
  [TL] Conv2dLayer gen_A2B/c40: shape:[3, 3, 20, 40] strides:[1, 2, 2, 1] pad:SAME act:identity
  [TL] InstanceNormLayer gen_A2B/ins3: epsilon:0.000010 act:relu
  [TL] Conv2dLayer gen_A2B/res/c1/0: shape:[3, 3, 40, 40] strides:[1, 1, 1, 1] pad:SAME act:identity
  [TL] InstanceNormLayer gen_A2B/res/ins/0: epsilon:0.000010 act:relu
  [TL] Conv2dLayer gen_A2B/res/c2/0: shape:[3, 3, 40, 40] strides:[1, 1, 1, 1] pad:SAME act:identity
  [TL] InstanceNormLayer gen_A2B/res/ins2/0: epsilon:0.000010 act:identity
  [TL] ElementwiseLayer gen_A2B/b_residual_add/0: size:(1, 55, 55, 40) fn:add
  [TL] Conv2dLayer gen_A2B/res/c1/1: shap

  [TL] InstanceNormLayer gen_A2B/ins1: epsilon:0.000010 act:relu
  [TL] Conv2dLayer gen_A2B/c20: shape:[3, 3, 10, 20] strides:[1, 2, 2, 1] pad:SAME act:identity
  [TL] InstanceNormLayer gen_A2B/ins2: epsilon:0.000010 act:relu
  [TL] Conv2dLayer gen_A2B/c40: shape:[3, 3, 20, 40] strides:[1, 2, 2, 1] pad:SAME act:identity
  [TL] InstanceNormLayer gen_A2B/ins3: epsilon:0.000010 act:relu
  [TL] Conv2dLayer gen_A2B/res/c1/0: shape:[3, 3, 40, 40] strides:[1, 1, 1, 1] pad:SAME act:identity
  [TL] InstanceNormLayer gen_A2B/res/ins/0: epsilon:0.000010 act:relu
  [TL] Conv2dLayer gen_A2B/res/c2/0: shape:[3, 3, 40, 40] strides:[1, 1, 1, 1] pad:SAME act:identity
  [TL] InstanceNormLayer gen_A2B/res/ins2/0: epsilon:0.000010 act:identity
  [TL] ElementwiseLayer gen_A2B/b_residual_add/0: size:(1, 8, 8, 40) fn:add
  [TL] Conv2dLayer gen_A2B/res/c1/1: shape:[3, 3, 40, 40] strides:[1, 1, 1, 1] pad:SAME act:identity
  [TL] InstanceNormLayer gen_A2B/res/ins/1: epsilon:0.000010 act:relu
  [TL] Conv2dLayer 

  [TL] Conv2dLayer dis_A/d40: shape:[3, 3, 20, 40] strides:[1, 2, 2, 1] pad:SAME act:identity
  [TL] InstanceNormLayer dis_A/ins3: epsilon:0.000010 act:relu
  [TL] Conv2dLayer dis_A/res/c1/0: shape:[3, 3, 40, 40] strides:[1, 2, 2, 1] pad:SAME act:identity
  [TL] InstanceNormLayer dis_A/res/ins1/0: epsilon:0.000010 act:relu
  [TL] Conv2dLayer dis_A/res/c2/0: shape:[3, 3, 40, 40] strides:[1, 1, 1, 1] pad:SAME act:identity
  [TL] InstanceNormLayer dis_A/res/ins2/0: epsilon:0.000010 act:relu
  [TL] Conv2dLayer dis_A/res/c3/0: shape:[3, 3, 40, 40] strides:[1, 1, 1, 1] pad:SAME act:identity
  [TL] InstanceNormLayer dis_A/res/ins3/0: epsilon:0.000010 act:identity
  [TL] ElementwiseLayer dis_A/b_residual_add/0: size:(1, 28, 28, 40) fn:add
  [TL] Conv2dLayer dis_A/res/c1/1: shape:[3, 3, 40, 80] strides:[1, 2, 2, 1] pad:SAME act:identity
  [TL] InstanceNormLayer dis_A/res/ins1/1: epsilon:0.000010 act:relu
  [TL] Conv2dLayer dis_A/res/c2/1: shape:[3, 3, 80, 80] strides:[1, 1, 1, 1] pad:SAME act:i

ValueError: Trying to share variable dis_A/d/h4/final/W, but specified shape (320, 1) and found shape (5120, 1).

In [9]:
train_A[0].shape

(220, 220, 1)

In [33]:

real_A = tf.placeholder(tf.float32, [1,220,220,1],name='real_A')
gen_A, gen_A_out= cyclegan_generator_resnet(real_A,batch_size=1)

#cycle_A, cycle_A_out=cyclegan_generator_resnet(gen_A_out,batch_size=1)





#gen_out=sess.run(gen_A_out,feed_dict={real_A:a})

#x=cyclegan_discriminator_patch(real_A)[1]
tf.reset_default_graph()
sess=tf.Session()
tf.reset_default_graph()


tl.layers.initialize_global_variables(sess)


sess.run(gen_A_out,feed_dict={real_A:train_A[0].reshape([1,220,220,1])})
print(gen_A_out)

Exception: Layer 'generator/in' already exists, please choice other 'name' or reuse this layer            
Hint : Use different name for different 'Layer' (The name is used to control parameter sharing)

In [39]:
tf.reset_default_graph()

In [40]:
tf.reset_default_graph()
b_init = tf.constant_initializer(value=0.0)
w_init = tf.truncated_normal_initializer(stddev=0.02)
g_init = tf.random_normal_initializer(1., 0.02)
a=tf.zeros([1,220,220,1])
gf_dim=10
batch_size=1

net_in = InputLayer(a, name='in')
        # net_pad = PadLayer(net_in, [[0, 0], [3, 3], [3, 3], [0, 0]], "REFLECT", name='inpad')


net_c1 = Conv2d(net_in, gf_dim, (7, 7), (1, 1), act=None,
                padding='SAME', W_init=w_init, name='c7s1-10')  # c7s1-10   shape:(1,257,258,10)
print("c1",net_c1.outputs.shape)



net_c2 = Conv2d(net_c1, gf_dim * 2, (3, 3), (2, 2), act=None,
                padding='SAME', W_init=w_init,name='d20')  # d64   shape:(1,129,129,20)
print( "c2",net_c2.outputs.shape)

net_c3 = Conv2d(net_c2, gf_dim * 4, (3, 3), (2, 2), act=None,
                padding='SAME', W_init=w_init, name='d40')  # d128   shape(1,65,65,40)
print( "c3", net_c3.outputs.shape)


n = net_c3

for i in range(9):
        # n_pad = PadLayer(n, [[0, 0], [1, 1], [1, 1], [0, 0]], "REFLECT", name='pad_%s' % i)
        nn = Conv2d(n, gf_dim * 4, (3, 3), (1, 1), act=None,
            padding='SAME', W_init=w_init, b_init=b_init, name='res/c1/%s' % i)

        # nn = PadLayer(nn, [[0, 0], [1, 1], [1, 1], [0, 0]], "REFLECT", name='pad2_%s' % i)
        nn = Conv2d(nn, gf_dim * 4, (3, 3), (1, 1), act=None,
            padding='SAME', W_init=w_init, b_init=b_init, name='res/c2/%s' % i)

        nn = ElementwiseLayer([n, nn], tf.add, name='b_residual_add/%s' % i)
        n = nn
        print( i, n.outputs.shape)


net_r9 = n
net_d1=DeConv2d(net_r9, gf_dim*2, (3, 3), out_size=(130,130),
    strides=(2, 2), padding='SAME',batch_size=batch_size, act=None, name='u64')
#net_d1 = tf.layers.conv2d_transpose(net_r9, gf_dim * 2, (3, 3), out_size=(129,129), strides=(2,2), padding='same', batch_size=batch_size, act=None, name='u64')  # u64


net_d2 = DeConv2d(net_d1, gf_dim, (3, 3), out_size=(260,260),
    strides=(2, 2), padding='SAME',batch_size=batch_size, act=None, name='u32')  # u32
print( "d2",net_d1.outputs.shape)

# net_d2_pad = PadLayer(net_d2, [[0, 0], [3, 3], [3, 3], [0, 0]], "REFLECT", name='pado')
net_d3 = Conv2d(net_d2, 1, (7, 7), (1, 1), act=tf.nn.tanh,
    padding='SAME', name='c7s1-3')  # c7s1-3
out=net_d3.outputs[:,:220,:220,:]
print( "d3",out)



Exception: Layer 'in' already exists, please choice other 'name' or reuse this layer            
Hint : Use different name for different 'Layer' (The name is used to control parameter sharing)

In [311]:

p,k=scipy.signal.istft(np.exp(B[3]),fs=22050,nfft=512,nperseg=512)
ipd.Audio(k,rate=22050)
print()

In [288]:
l, sr = lbr.load('./blues.00051.au',sr=None)
print(l.shape)
ipd.Audio(l, rate=sr)

(661794,)


In [289]:
f,t,m = scipy.signal.stft(l,fs=22050,nfft=512,nperseg=512)
print(m.shape)
p=np.exp(np.log(m[:,0:m.shape[1]*25//30]))
a,t=scipy.signal.istft(p,fs=22050)
ipd.Audio(t,rate=sr)


(257, 2587)
